In [42]:
import numpy as np
import trimesh
import networkx as nx
import scipy
import matplotlib.pyplot as plt
import robust_laplacian
import os

In [2]:
# gr : nx Graph
# k : k-largest eigenvalues

# returns:
# ndarray with shape (k,)
# k eigenvalues

# ndarray with shape (N, k)
# for N = number of nodes in gr 
#     k = number of eigenvalues 
def laplacian_eigenmap(gr, k, lap=None):
    lap = nx.laplacian_matrix(gr)
    lap = lap.asfptype()
    eigs = scipy.sparse.linalg.eigsh(lap, k=k)
    e_vals = eigs[0]
    e_vecs = eigs[1]
    
    return e_vals, e_vecs

In [3]:
def mesh_laplacian_eigenmap(verts, faces, k, lap=None):
    L, M = robust_laplacian.mesh_laplacian(verts, faces)
    # L = L.asfptype()
    eigs = scipy.sparse.linalg.eigsh(L, k, M)
    e_vals = eigs[0]
    e_vecs = eigs[1]
    
    return e_vals, e_vecs

In [4]:
def get_dists(obj1, obj2):
    if obj1.vertices.shape[0] != obj2.vertices.shape[0]:
        raise Exception('objects are not one-to-one')
    
    offsets = np.zeros(obj1.vertices.shape[0])
    for i, face in enumerate(obj1.vertices):
        offsets[i] = np.linalg.norm(obj1.vertices[i]-obj2.vertices[i])
    return offsets

In [5]:
def get_offsets(obj1, obj2):
    if obj1.vertices.shape[0] != obj2.vertices.shape[0]:
        raise Exception('objects are not one-to-one')
    
    offsets = np.zeros((obj1.vertices.shape[0], 3))
    for i, face in enumerate(obj1.vertices):
        offsets[i] = obj1.vertices[i]-obj2.vertices[i]
    return offsets

In [31]:
# smoothes a mesh using trimesh laplacian smoothing
def smooth_mesh_tm(mesh, iterations):
    orig = mesh
    smooth = mesh.copy()
    smooth = trimesh.smoothing.filter_laplacian(smooth, iterations=iterations)
    
    return smooth, orig

In [2]:
def build_offset_dataset(mesh, smooth_iter=200, lap_type='std'):
    smooth, orig = smooth_mesh_tm(mesh, iterations=smooth_iter)
    offsets = get_offsets(smooth, orig)
    
    if lap_type == 'mesh':
        e_vals, e_vecs = mesh_laplacian_eigenmap(np.array(smooth.vertices), np.array(smooth.faces), 100)
    else:
        gr = smooth.vertex_adjacency_graph
        e_vals, e_vecs = laplacian_eigenmap(gr, 100)
    
    dataset = {
        'fourier' : e_vecs,
        'points' : smooth.vertices,
        'target' : offsets      
          }
    return dataset, smooth

In [1]:
def build_blank_dataset(blank, DIR_NAME, lap_type='std'):
    if lap_type == 'mesh':
        e_vals, e_vecs = mesh_laplacian_eigenmap(np.array(blank.vertices), np.array(blank.faces), 100)
    else:
        gr = blank.vertex_adjacency_graph
        e_vals, e_vecs = laplacian_eigenmap(gr, 100)
    
    dataset = {
    'fourier' : e_vecs,
    'target' : np.zeros(blank.vertices.shape[0]),
    'points' : blank.vertices   
          }
    
    if not os.path.exists(f'{DIR_NAME}/npz_files'):
        os.makedirs(f'{DIR_NAME}/npz_files')
    np.savez(f'{DIR_NAME}/npz_files/{DIR_NAME}', fourier=dataset['fourier'], points=dataset['points'], target=dataset['target'])
    
    return f'/Users/maxperozek/GINR-texture/{DIR_NAME}'

In [11]:
def get_sphere(size=0):
    sphere = trimesh.primitives.Sphere()
    if size > 0:
        new_verts, new_faces = trimesh.remesh.subdivide_loop(sphere.vertices, sphere.faces, iterations=size)
        sphere = trimesh.Trimesh(vertices=new_verts, faces=new_faces)
    return sphere

In [8]:
def generate_pred_mesh(offset_preds, blank):
    pred_verts =  blank.vertices + offset_preds['preds']
    inference = trimesh.Trimesh(vertices=pred_verts, faces=blank.faces)
    inference = trimesh.repair.fill_holes(inference)
    return inference

### Run experiments

In [76]:
# load the texture sample as well as the blank (sphere/ cube/ simple untextured shape
texture = trimesh.load('/Users/maxperozek/GINR-texture/Spikey_ball_or_massage_ball_or_toy_4357441/files/half_ball.stl')
blank = get_sphere(size=3)
print(texture.vertices.shape[0])
print(blank.vertices.shape[0])

31760
40962


In [77]:
BLANK_DATASET = build_blank_dataset(blank, 'blank_sphere')

In [78]:
texture.show()

In [79]:
blank.show()

In [80]:
dataset, smooth = build_offset_dataset(texture, smooth_iter=1000)

In [37]:
# ensure that the smoothed texture is 'smooth enough'
smooth.show()

In [43]:
# save TEXTUER training dataset
DIRECTORY_NAME = 'half_spike'
if not os.path.exists(f'{DIRECTORY_NAME}/npz_files'):
    os.makedirs(f'{DIRECTORY_NAME}/npz_files')
np.savez(f'{DIRECTORY_NAME}/npz_files/{DIRECTORY_NAME}', fourier=dataset['fourier'], points=dataset['points'], target=dataset['target'])

Now run the following command from GINR repo:

In [47]:
cmd = f'python train_ginr.py --dataset_dir /Users/maxperozek/GINR-texture/{DIRECTORY_NAME} --n_fourier 100 --n_nodes_in_sample {texture.vertices.shape[0]} --lr 0.0001 --n_layers 6 --skip=True --sine=True --all_sine=True'
print(cmd)


python train_ginr.py --dataset_dir /Users/maxperozek/GINR-texture/half_spike --n_fourier 100 --n_nodes_in_sample 31760 --lr 0.0001 --n_layers 6 --skip=True --sine=True --all_sine=True


Now run inference with:

In [83]:
# get best checkpoint path from GINR/lightning_logs/version_xx/checkpoints/best.ckpt
BEST_CHECKPOINT_PATH = '/Users/maxperozek/GINR/lightning_logs/version_12/checkpoints/best.ckpt'

In [84]:
cmd = f'python eval_ginr.py {BEST_CHECKPOINT_PATH} --dataset_dir {BLANK_DATASET} --n_fourier 100'
print(cmd)

python eval_ginr.py /Users/maxperozek/GINR/lightning_logs/version_12/checkpoints/best.ckpt --dataset_dir /Users/maxperozek/GINR-texture/blank_sphere --n_fourier 100


In [85]:
# unfortunately this is hard-coded at the moment
# offset_preds = np.load('/Users/maxperozek/GINR/preds.npz')
offset_preds = np.load('/Users/maxperozek/GINR/golf_sphere_preds.npz')

In [86]:
pred_verts = blank.vertices + offset_preds['preds']

In [87]:
inference = trimesh.Trimesh(vertices=pred_verts, faces=blank.faces)

In [88]:
inference.show()